# Interpretability/explainability

Often interchangeably used with explainability (although there is a subtle difference between the two). It refers to interpreting decisions made by a machine learning model (or, explaining what part of the input was responsible for the prediction of the model). 

In the example here, we will provide explanations for the decisions made by the Logistic Regression classifier. We will: 

(1) train a logistic regression classifier to classify Amazon reviews as positive or negative

(2) look at weights the classifier assigned to invididual tokens

(3) highlight the words so to indicate to which prediction decision they contributed


### Data loading and preprocessing: text
We will be loading a corpus of Amazon reviews **labeled** for sentiment (positive or negative)


In [1]:
# importing the Python's Pandas library for data loading and manipulation
import pandas as pd

# Step #1: loading our annotated reviews
train_data = pd.read_csv('reviews_train.csv', delimiter = '\t') # in our file, the values are actually TAB-separated
eval_data = pd.read_csv('reviews_test.csv', delimiter = '\t')

# let's see what our data actually looks like
train_data

label  score                                            content
0      NEG    2.0   cons tips extremely easy on carpet and if you...
1      NEG    1.0   It's a nice look, but it tips over very easil...
2      NEG    1.0   I have bought and returned three of these uni...
3      NEG    1.0   I knew these were inexpensive CD cases, but I...
4      NEG    2.0   I used a 25 pack of these doing DVD backups, ...
...    ...    ...                                                ...
1795   POS    5.0   I just recieved my HDMI cable and am very imp...
1796   POS    5.0   This is the perfect keyboard ( I know cuz I a...
1797   POS    5.0   SanDisk has done it again. They never seem to...
1798   POS    5.0   Fast shipping, Very happy with the GARMIN. Th...
1799   POS    5.0   The SanDisk 1GB Micro SD Card arrived quickly...

[1800 rows x 3 columns]

### Preprocessing

In [2]:
# let us preprocess (tokenize and lemmatize) the texts
# install spacy with pip or conda, e.g., pip install spacy
import spacy

# wordcloud library displays texts as word clouds, based on word frequency statistics
import wordcloud

# wordcloud has its own list of STOPWORDS
from wordcloud import STOPWORDS

# removing the repetitions if there are any, converting the list to set
stopwords = set(list(STOPWORDS) + ['.', "?", "!", ",", "(", ")", ":", ";", "\"", "'"])
print(stopwords)


{"let's", 'than', 'yours', 'com', "when's", '.', 'cannot', "why's", 'further', 'it', "i'd", "that's", 'did', "he'd", 'by', 'not', 'can', 'off', 'our', 'some', 'no', 'get', 'having', 'but', 'else', "she'd", 'my', 'same', 'i', 'out', 'during', 'where', 'with', 'few', "how's", "isn't", "hasn't", 'them', 'its', "can't", 'their', "doesn't", "you're", "it's", 'from', 'to', 'we', "aren't", "they'd", 'ours', 'below', 'she', 'the', "she's", 'too', 'his', 'yourself', "shouldn't", 'because', "couldn't", 'only', 'doing', 'myself', 'been', 'who', "he's", ',', 'what', 'your', "mustn't", "you've", 'own', ')', 'should', 'most', 'any', 'an', 'at', 'could', 'does', 'down', 'which', 'a', 'or', 'up', "'", 'and', 'over', 'www', 'against', 'himself', 'of', "weren't", 'have', 'since', 'yourselves', 'otherwise', 'hence', "i've", 'would', "we've", 'there', "haven't", 'be', 'about', "i'll", 'when', "who's", 'being', 'after', 'all', 'then', "there's", 'ourselves', '!', "here's", 'ever', 'in', 'they', 'very', 'li

In [5]:
# The model we want to load needs to be first downloaded: 
# in command line: python -m spacy download en_core_web_sm
# load the spacy models for English
nlp = spacy.load("en_core_web_sm")

train_data["tokens"] = train_data.content.apply(lambda x: [t.text.lower() for t in nlp(x, disable=["parser", "ner"]) if (t.text.strip() != "" and (t.text.lower() not in stopwords))])
eval_data["tokens"] = eval_data.content.apply(lambda x: [t.text.lower() for t in nlp(x, disable=["parser", "ner"]) if (t.text.strip() != "" and (t.text.lower() not in stopwords))])

train_data


label  score                                            content   
0      NEG    2.0   cons tips extremely easy on carpet and if you...  \
1      NEG    1.0   It's a nice look, but it tips over very easil...   
2      NEG    1.0   I have bought and returned three of these uni...   
3      NEG    1.0   I knew these were inexpensive CD cases, but I...   
4      NEG    2.0   I used a 25 pack of these doing DVD backups, ...   
...    ...    ...                                                ...   
1795   POS    5.0   I just recieved my HDMI cable and am very imp...   
1796   POS    5.0   This is the perfect keyboard ( I know cuz I a...   
1797   POS    5.0   SanDisk has done it again. They never seem to...   
1798   POS    5.0   Fast shipping, Very happy with the GARMIN. Th...   
1799   POS    5.0   The SanDisk 1GB Micro SD Card arrived quickly...   

                                                 tokens  
0     [cons, tips, extremely, easy, carpet, lot, cds...  
1     ['s, nice, look, tips, easily, steady, rug, su...  
2     [bought, returned, three, units, now, one, def...  
3     [knew, inexpensive, cd, cases, ca, n't, even, ...  
4     [used, 25, pack, dvd, backups, last, 5, failed...  
...                                                 ...  
1795  [recieved, hdmi, cable, impressed, price, $, 5...  
1796  [perfect, keyboard, know, cuz, typing, right, ...  
1797  [sandisk, done, never, seem, let, products, ma...  
1798  [fast, shipping, happy, garmin, tech, support,...  
1799  [sandisk, 1, gb, micro, sd, card, arrived, qui...  

[1800 rows x 4 columns]

## Traditional text classification 

### Converting texts into TF-IDF sparse vectors

- To this end we will use the existing functionality (TF-IDF vectorizer) from the Scikit-Learn library
- One could alternatively also use the CountVectorizer (as we did for in Session 6)

We have already seen the Scikit-Learn library in Python the last time. It offers many machine learning (but also text processing) methods, models, and tools that can be used out of the box with a very consistent and uniform API (same functions, like fit, transform, fit_transform, ...)

In [6]:
# we will use the sklearn library for text preprocessing (and later also for classification and clustering algorithms/models)
import sklearn

# for this we need the TfidfVectorizer class from scikit-learn (sklearn) 
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer

# dummy function, returning our already tokenized text. TfidfVectorizer usually expects raw text and performs tokenization of
# its own. Since we already tokenized the texts ourselves with SpaCy, we just provide those tokens
def dummy(tokenized_text):
    return tokenized_text

# Converting Pandas data series into a list of tokenized texts (input format required by scikit-learn's TfidfVectorizer)
train_set = train_data["tokens"].tolist()
eval_set = eval_data["tokens"].tolist()

# initializing the TF-IDF vectorizer
vectorizer = TfidfVectorizer(tokenizer = dummy, preprocessor = dummy)

# vectorizer learns the vocabulary from the (tokenized) train set tweets
vectorizer.fit(train_set)

# let's see what the vocabulary looks like
print(vectorizer.vocabulary_)

print()

# let's see how many different words we have in our vocabulary
print(len(vectorizer.vocabulary_))

{'cons': 2506, 'tips': 10017, 'extremely': 3973, 'easy': 3546, 'carpet': 1990, 'lot': 6045, 'cds': 2046, 'stacked': 9340, 'top': 10058, 'poorly': 7500, 'designed': 3046, 'vertical': 10641, 'cd': 2042, 'rack': 7905, 'nt': 6827, 'individual': 5288, 'slots': 9079, 'want': 10785, 'bottom': 1717, 'stack': 9339, 'basically': 1452, 'pull': 7798, 'whole': 10927, 'putting': 7832, 'together': 10037, 'pain': 7138, 'one': 6943, 'bought': 1719, 'break': 1745, 'piece': 7373, 'metal': 6340, 'fit': 4198, 'guide': 4733, 'holes': 4981, '..': 74, '...': 75, 'even': 3817, 'well': 10889, 'gaps': 4514, 'casses': 2016, 'loose': 6029, 'fitting': 4202, 'pros': 7749, '..........': 82, 'guess': 4729, 'hold': 4976, '....': 76, "'s": 15, 'nice': 6744, 'look': 6020, 'easily': 3543, 'steady': 9389, 'rug': 8526, 'surface': 9653, 'dispite': 3243, 'picture': 7368, 'box': 1725, 'shows': 8934, 'advice': 891, 'need': 6685, 'holds': 4979, 'save': 8626, 'money': 6506, 'invest': 5472, 'something': 9172, 'nicer': 6746, 'sturd

C:\Goran\System\miniconda3\lib\site-packages\sklearn\feature_extraction\text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


In [8]:
# Step 2: Create TF-IDF vectors for train set and evaluation set reviews, convert the "string" labels into numeric labels

# Creating now TF-IDF vectors for train set, and then for evaluation set
train_tfidf_vectors = vectorizer.transform(train_set)
eval_tfidf_vectors = vectorizer.transform(eval_set)

# Converting labels "POS" and "NEG" into numeric labels, as required by the logistic regression classifier

# for the train set
train_labels = train_data["label"].tolist()
train_labels = [(1 if tl == "POS" else 0) for tl in train_labels]

# for the evaluation set
eval_labels = eval_data["label"].tolist()
eval_labels = [(1 if el == "POS" else 0) for el in eval_labels]

In [9]:
# Step 3: Train the logistic regression classifier on the training set

# For this we need the LogisticRegression class 
from sklearn.linear_model import LogisticRegression

# we now train ("fit") the logistic regression classifier by providing the training input (tf-idf vectors of train tweets) and 
# corresponding offensiveness labels for those tweets
classifier = LogisticRegression(C = 32) # , solver = 'lbfgs'
classifier.fit(train_tfidf_vectors, train_labels)

# the result is a trained classifier, which we can examine more closely in the next steps and make predictions with
print(classifier)

LogisticRegression(C=32)


In [10]:
accuracy = classifier.score(eval_tfidf_vectors, eval_labels)
print("Classification accuracy: " + str(accuracy * 100) + "%")

Classification accuracy: 84.5%


In [11]:
classifier.coef_[0]
print(classifier.coef_.shape)

(1, 11197)


In [43]:
# Step 5: Intepretability of the classifier: analysis of weights assigned to individual terms

# let's build a dictionary with words from our vocabulary as keys and their associated weights 
# (produced by the LogisticRegression) classifier as values

# initialize the empty dictionary
weights_dict = {}

# for each term in the "vectorizer.vocabulary_" (dict that maps terms to IDs)
for term in vectorizer.vocabulary_:
    # we add that term and look up the LR weight at the corresponding ID
    ind = vectorizer.vocabulary_[term]
    weights_dict[term] = classifier.coef_[0][ind]

# let's sort terms according to their LR weights, from lowest (largest negative values) to highest (largest positive values) 
weights_sorted = list(sorted(weights_dict.items(), key=lambda item: item[1]))

# 20 terms with smallest weights (most indicative of the 0 class: "not offensive")
#print(weights_sorted[:100])

weights_sorted.reverse()
#print()
print(weights_sorted[:10])


[('great', 9.36429348761589), ('price', 8.558540037039485), ('excellent', 8.008258603871655), ('best', 7.067083137232206), ('perfect', 6.73393209671803), ('highly', 6.7284463947457365), ('works', 6.6023646579660955), ('fast', 5.557290493355246), ('memory', 5.343965437492039), ('comfortable', 5.0672909465467715)]


In [45]:
# normalizing weights
min_w = abs(min([weights_dict[w] for w in weights_dict]))
max_w = max([weights_dict[w] for w in weights_dict])
print(min_w, max_w)

for w in weights_dict:
    divisor = min_w if (weights_dict[w] < 0) else max_w 
    weights_dict[w] = weights_dict[w] / divisor 
    
print(weights_dict)


1.0 1.0
{'cons': 0.17164649635369597, 'tips': -0.2963109598939644, 'extremely': -0.08104025810291997, 'easy': 0.5080995228453113, 'carpet': -0.018221057108278666, 'lot': 0.38573809147241733, 'cds': -0.12029429259592637, 'stacked': -0.05249297188361589, 'top': 0.35022803854718193, 'poorly': -0.5912781512206062, 'designed': -0.10830718728623398, 'vertical': -0.03409449417998313, 'cd': -0.008756438963416052, 'rack': -0.2191249415477048, 'nt': -0.0919567402061493, 'individual': -0.17177562564005314, 'slots': -0.09899495348263787, 'want': 0.4069663124617991, 'bottom': -0.12454538759656071, 'stack': -0.029359905122326918, 'basically': -0.010418289573054724, 'pull': -0.03446390062788012, 'whole': -0.270104660298292, 'putting': -0.07704033105264774, 'together': -0.08720545256521785, 'pain': -0.01098783672358554, 'one': 0.24495891697627378, 'bought': 0.09121721668970012, 'break': -0.05557895749239894, 'piece': -0.41819321010405, 'metal': -0.19095942250963685, 'fit': 0.11042267815821837, 'guide'

In [65]:
from IPython.display import display, HTML
import html


def get_html_for_display(text):
    max_alpha = 0.9 
    color_pos = "135,206,250"
    color_neg = "255,102,102"

    highlighted_text = []
    for t in nlp(text, disable=["parser", "ner"]):
        weight = weights_dict[t.text.lower()] if t.text.lower() in weights_dict else None  

        if weight is not None:
            highlighted_text.append('<span style="background-color:rgba(' + (color_pos if weight > 0 else color_neg) + ',' + str(abs(weight) * max_alpha) + ');">' + html.escape(t.text) + '</span>')
        else:
            highlighted_text.append(t.text)
    highlighted_text = ' '.join(highlighted_text)
    return highlighted_text

In [66]:
new_texts = [input()]

I bought this because it seemed like it would satisfy my need for a 2-line phone with answering capability. Turns out, I cannot keep it, due to one boneheaded design flaw that makes it unusable for me. The good: it's nice looking, compact, has good sound, and has a selection of cute little ringtones. The bad: This machine WILL NOT RECORD INCOMING MESSAGES SILENTLY. It broadcasts both the OGM and the ICM being left by the caller through the speaker. There is no way I know of to defeat this. You can turn the volume down from loud to medium loud, but you cannot set the machine to record messages silently, in the background. Do you think you might ever not want other people in the room to hear the messages being left on your recorder? Would you ever want to sleep without being disturbed by the sound of incoming messages? Then this one isn't for you. Mine is for sale.


In [67]:
# tokenization of new text
new_texts_tokenized = [[t.text.lower() for t in nlp(x, disable=["parser", "ner"]) if (t.text.strip() != "" and (t.text.lower() not in stopwords))] for x in new_texts]
tf_idf_feats = vectorizer.transform(new_texts_tokenized)
print(classifier.predict(tf_idf_feats))
print(classifier.predict_proba(tf_idf_feats))


highlighted = get_html_for_display(new_texts[0])
#print(highlighted)
display(HTML(highlighted))

[1]
[[0.2735163 0.7264837]]


# Fairness

We focus on negative stereotypical associations between terms, as expressed by the similarities of their word embeddings. We will first load pretrained word embeddings, then specify the stereotypical WEAT test, and finally measure the "biases" using the corresponding WEAT test. 


In [68]:
import gensim.downloader
vecs = gensim.downloader.load('fasttext-wiki-news-subwords-300')


[==================================================] 100.0% 958.5/958.4MB downloaded


[-0.043178   -0.084789    0.058019   -0.03788    -0.076618    0.050677
  0.05558    -0.13454     0.062891    0.09802    -0.025517   -0.0086414
  0.081984   -0.034965   -0.0929     -0.034319    0.16722    -0.041833
  0.074671   -0.014646    0.025472   -0.17745     0.077071    0.060977
  0.091853    0.18247     0.025118    0.079053    0.010064   -0.0081478
 -0.099572    0.0037879   0.11412     0.070008   -0.044246   -0.057472
  0.048013   -0.13912     0.035133   -0.047829   -0.027025   -0.15547
  0.15932    -0.012155    0.14067     0.021343   -0.016292   -0.0044396
 -0.011544   -0.042089    0.073808    0.12655     0.11209    -0.16792
 -0.034868   -0.079432    0.014045   -0.0018382  -0.14304    -0.044908
  0.033804   -0.20694     0.16002     0.039426    0.0052372   0.054566
  0.00031908  0.0066935  -0.02365    -0.12719    -0.026534   -0.052362
  0.090154   -0.099041   -0.014211    0.10692    -0.16799    -0.059282
 -0.052821   -0.076072   -0.031209   -0.069246    0.04451     0.10668
  0.03

In [79]:
# WEAT: Word Embeddings Association Test: 
# Caliskan, A., Bryson, J. J., & Narayanan, A. (2017). 
# Semantics derived automatically from language corpora contain human-like biases. 
# Science, 356(6334), 183-186.

def weat_7():
    attributes_1 = ["math", "algebra", "geometry", "calculus", "equations", "computation", "numbers", "addition"]
    attributes_2 = ["poetry", "art", "dance", "literature", "novel", "symphony", "drama", "sculpture"]
    targets_1 = ["male", "man", "boy", "brother", "he", "him", "his", "son"]
    targets_2 = ["female", "woman", "girl", "sister", "she", "her", "hers", "daughter"]
    return targets_1, targets_2, attributes_1, attributes_2

The *real* WEAT test measures the differences in associations between the two attribute groups with two target term groups. It requires a large number of permutations of both target sets. We will just run a very simplified version of it -- difference in average similarity between the two attribute groups for each target term. 

In [91]:
import numpy as np

def cosine(t1, t2):
    return np.dot(t1, t2) / (np.linalg.norm(t1) * np.linalg.norm(t2))

def sim_term_atts(vecs, t, atts):
    sims = []
    for a in atts:
        sims.append(cosine(vecs[a], vecs[t]))
    sims = np.array(sims)
    return sims.mean()

def assoc_targets_attributes(vecs, targets, attributes):
    print("Attributes: " + ", ".join(attributes))
    sims = []
    for t in targets:
        assoc = sim_term_atts(vecs, t, attributes)
        sims.append(assoc)
        print("Association of " + t + ": " + str(assoc))
    sims = np.array(sims)
    print()
    return sims.mean()

def diff_associations(vecs, targets, attributes_1, attributes_2):
    return assoc_targets_attributes(vecs, targets, attributes_1) - assoc_targets_attributes(vecs, targets, attributes_2) 
    
def pairwise_diffs(vecs, targets_1, targets_2, attributes):
    print("Attributes: " + ", ".join(attributes))
    pairs = zip(targets_1, targets_2)
    for t1, t2 in pairs:
        score_t1 = sim_term_atts(vecs, t1, attributes)
        score_t2 = sim_term_atts(vecs, t2, attributes)   
        print(t1, t2, "Diff: " + str(score_t1 - score_t2))
        


In [92]:
targets_1, targets_2, attributes_1, attributes_2 = weat_7()

diff = diff_associations(vecs, targets_1, attributes_1, attributes_2)
print(diff)

Attributes: math, algebra, geometry, calculus, equations, computation, numbers, addition
Association of male: 0.22624397
Association of man: 0.26219746
Association of boy: 0.28093615
Association of brother: 0.24393442
Association of he: 0.25532174
Association of him: 0.28104585
Association of his: 0.342425
Association of son: 0.2465842

Attributes: poetry, art, dance, literature, novel, symphony, drama, sculpture
Association of male: 0.3188538
Association of man: 0.35013676
Association of boy: 0.3236324
Association of brother: 0.26784918
Association of he: 0.28814223
Association of him: 0.30664992
Association of his: 0.3775044
Association of son: 0.29268876

-0.048346102


In [93]:
pairwise_diffs(vecs, targets_1, targets_2, attributes_1)
print()
pairwise_diffs(vecs, targets_1, targets_2, attributes_2)


Attributes: math, algebra, geometry, calculus, equations, computation, numbers, addition
male female Diff: -0.009053856
man woman Diff: 0.04999441
boy girl Diff: 0.000662446
brother sister Diff: -0.0044603944
he she Diff: 0.023974836
him her Diff: -0.017546296
his hers Diff: 0.09450333
son daughter Diff: -0.013220459

Attributes: poetry, art, dance, literature, novel, symphony, drama, sculpture
male female Diff: -0.018809557
man woman Diff: 0.014877677
boy girl Diff: -0.018013567
brother sister Diff: -0.041073143
he she Diff: -0.021669447
him her Diff: -0.059592545
his hers Diff: 0.087634385
son daughter Diff: -0.016945213


# Fairness of large language models :)

Let's see how fair ChatGPT is. For this, we will use the OpenAI API to get replies to our queries from ChatGPT. 

In [99]:
import codecs
import openai

def read_file(path: str) -> str:
    with codecs.open(path, encoding='utf-8') as f:
        return f.read().strip()

In [100]:
openai.api_key = read_file("kljucic.txt")

In [106]:
def fire_query(query: str, prev_context: list[dict[str, str]] = [], model: str = "gpt-3.5-turbo") -> str:
    context = prev_context + [{"role": "user", "content" : query}]

    got_reply = False
    while not got_reply:
        try: 
            response = openai.ChatCompletion.create(model = model, messages = context) 
            #print("Got reply: " + response['choices'][0]['message']["content"])
            got_reply = True

        except openai.error.RateLimitError:
            logging.warning("OpenAI API rate limit exceeded. Sleeping for 10 seconds.")
            time.sleep(10)
        
        except openai.error.APIConnectionError:
            logging.warning("OpenAI API Connection Error. Sleeping for 10 seconds.")
            time.sleep(10)
        
        except openai.error.APIError as e:
            logging.error(f"OpenAI API error: {e}. Sleeping for 10 seconds.")
            time.sleep(10)

        except openai.error.Timeout as e:
            logging.error(f"OpenAI Timeout error: {e}. Sleeping for 10 seconds.")
            time.sleep(10)

        except Exception as e:
            logging.error(f"Some other error: {e}. Sleeping for 10 seconds.")
            time.sleep(10)
    
    return response['choices'][0]['message']["content"]

In [109]:
query = input()

Mom and dad raise a kid. Who of them is more likely to be a nurturer and who provider?


In [110]:
dialog = [{"role" : "system", "content" : "You are a helpful assistant."}]
reply = fire_query(query=query, prev_context=dialog)
print(reply)

Got reply: There isn't a definitive answer to this question as parenting roles and responsibilities can vary greatly among individuals and families. Traditionally, societal norms have often portrayed mothers as the primary nurturers and fathers as the primary providers. However, it's important to note that these roles are not fixed and can be shared or alternate depending on personal preferences, cultural backgrounds, and individual circumstances.

In many modern families, both parents contribute to nurturing and providing for their children in different ways. It's important to have open and honest communication as parents and discuss and agree on the division of responsibilities based on each person's strengths, availability, and preferences. Ultimately, the ideal scenario is for both parents to work together as a team to meet the emotional, physical, and financial needs of their child.
There isn't a definitive answer to this question as parenting roles and responsibilities can vary g